# Supplement with correlations between ID - RD and OOD - RD

In [2]:
from pathlib import Path
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import math

from NegativeClassOptimization import datasets, ml, visualisations
from NegativeClassOptimization import utils, config
from NegativeClassOptimization import preprocessing

/home/eugen/miniconda3/envs/nco/lib/python3.8/site-packages/sklearn/preprocessing/_encoders.py:972: FutureWarning: `sparse` was renamed to `sparse_output` in version 1.2 and will be removed in 1.4. `sparse_output` is ignored unless you leave `sparse` to its default value.
  warnings.warn(
/home/eugen/miniconda3/envs/nco/lib/python3.8/site-packages/sklearn/preprocessing/_encoders.py:972: FutureWarning: `sparse` was renamed to `sparse_output` in version 1.2 and will be removed in 1.4. `sparse_output` is ignored unless you leave `sparse` to its default value.
  warnings.warn(


In [3]:
df_id = pd.read_csv(
    "../data/closed_performance.tsv",
    sep='\t'
)
df_id["task_type"] = df_id["task"].apply(lambda x: datasets.ClassificationTask.init_from_str(x).task_type.to_str())
df_id["ag_pos"] = df_id["task"].apply(lambda x: datasets.ClassificationTask.init_from_str(x).ag_pos)
df_id["ag_neg"] = df_id["task"].apply(lambda x: datasets.ClassificationTask.init_from_str(x).ag_neg)

df_id.head(5)

task       acc  recall  precision        f1  \
0   HIGH_VS_95LOW__3VRL__auto__0__42  0.996600  0.9980   0.995213  0.996605   
1  HIGH_VS_LOOSER__3VRL__auto__0__42  0.953400  0.9604   0.947140  0.953724   
2     ONE_VS_NINE__3VRL__auto__0__42  0.972986  0.9750   0.971116  0.973054   
3   HIGH_VS_95LOW__3VRL__auto__1__42  0.996200  0.9986   0.993830  0.996209   
4  HIGH_VS_LOOSER__3VRL__auto__1__42  0.952600  0.9576   0.948119  0.952836   

        task_type ag_pos ag_neg  
0   high_vs_95low   3VRL   auto  
1  high_vs_looser   3VRL   auto  
2             1v9   3VRL   auto  
3   high_vs_95low   3VRL   auto  
4  high_vs_looser   3VRL   auto

In [4]:
df_ood = pd.read_csv(
    "../data/openset_performance.tsv",
    sep='\t',
)

df_ood["ag_1_pos"] = df_ood["task_1"].apply(lambda x: datasets.ClassificationTask.init_from_str(x).ag_pos)
df_ood["ag_2_pos"] = df_ood["task_2"].apply(lambda x: datasets.ClassificationTask.init_from_str(x).ag_pos)
df_ood["ag_1_neg"] = df_ood["task_1"].apply(lambda x: datasets.ClassificationTask.init_from_str(x).ag_neg)
df_ood["ag_2_neg"] = df_ood["task_2"].apply(lambda x: datasets.ClassificationTask.init_from_str(x).ag_neg)

df_ood["seed_1"] = df_ood["task_1"].apply(lambda x: datasets.ClassificationTask.init_from_str(x).seed_id)
df_ood["seed_2"] = df_ood["task_2"].apply(lambda x: datasets.ClassificationTask.init_from_str(x).seed_id)
df_ood["split_1"] = df_ood["task_1"].apply(lambda x: datasets.ClassificationTask.init_from_str(x).split_id)
df_ood["split_2"] = df_ood["task_2"].apply(lambda x: datasets.ClassificationTask.init_from_str(x).split_id)

assert df_ood.query("ag_1_pos != ag_2_pos").shape[0] == 0
df_ood["ag"] = df_ood["ag_1_pos"]

df_ood["task_1_type"] = df_ood["task_1"].apply(lambda x: datasets.ClassificationTask.init_from_str(x).task_type.to_str())
df_ood["task_2_type"] = df_ood["task_2"].apply(lambda x: datasets.ClassificationTask.init_from_str(x).task_type.to_str())

df_ood.head(5)

task_1                             task_2  \
0  HIGH_VS_95LOW__3VRL__auto__0__42   HIGH_VS_95LOW__3VRL__auto__0__42   
1  HIGH_VS_95LOW__3VRL__auto__0__42  HIGH_VS_LOOSER__3VRL__auto__0__42   
2  HIGH_VS_95LOW__3VRL__auto__0__42     ONE_VS_NINE__3VRL__auto__0__42   
3  HIGH_VS_95LOW__3VRL__auto__0__42   HIGH_VS_95LOW__3VRL__auto__1__42   
4  HIGH_VS_95LOW__3VRL__auto__0__42  HIGH_VS_LOOSER__3VRL__auto__1__42   

        acc  recall  precision        f1 ag_1_pos ag_2_pos ag_1_neg ag_2_neg  \
0  0.996600   0.998   0.995213  0.996605     3VRL     3VRL     auto     auto   
1  0.758500   0.998   0.674780  0.805163     3VRL     3VRL     auto     auto   
2  0.912356   0.998   0.852117  0.919307     3VRL     3VRL     auto     auto   
3  0.996600   0.998   0.995213  0.996605     3VRL     3VRL     auto     auto   
4  0.758500   0.998   0.674780  0.805163     3VRL     3VRL     auto     auto   

   seed_1  seed_2  split_1  split_2    ag    task_1_type     task_2_type  
0       0       0       42       42  3VRL  high_vs_95low   high_vs_95low  
1       0       0       42       42  3VRL  high_vs_95low  high_vs_looser  
2       0       0       42       42  3VRL  high_vs_95low             1v9  
3       0       1       42       42  3VRL  high_vs_95low   high_vs_95low  
4       0       1       42       42  3VRL  high_vs_95low  high_vs_looser

In [5]:
df_rd_logits = pd.read_csv(
    "../data/Frozen_MiniAbsolut_ML/07e_LogitEnergyCorrelations_final.tsv",
)
df_rd_logits["rd_type"] = "logits"
df_rd_logits["rd_metric"] = df_rd_logits["r_pos"]
df_rd_logits.head(20)

Unnamed: 0 task_type ag_pos ag_neg  seed_id  split_id         r  \
0            0       1v1   3VRL   1NSN        0        42 -0.585052   
1            1       1v1   3VRL   3RAJ        0        42 -0.334859   
2            2       1v1   3VRL   5E94        0        42 -0.151120   
3            3       1v1   3VRL   1H0D        0        42 -0.522465   
4            4       1v1   3VRL   1WEJ        0        42 -0.537149   
5            5       1v1   3VRL   1ADQ        0        42 -0.480855   
6            6       1v1   3VRL   1FBI        0        42 -0.365283   
7            7       1v1   3VRL   2YPV        0        42 -0.581685   
8            8       1v1   3VRL   1OB1        0        42 -0.613358   
9            9       1v1   1NSN   3VRL        0        42  0.312892   
10          10       1v1   1NSN   3RAJ        0        42  0.259787   
11          11       1v1   1NSN   5E94        0        42  0.193571   
12          12       1v1   1NSN   1H0D        0        42  0.005690   
13          13       1v1   1NSN   1WEJ        0        42  0.275205   
14          14       1v1   1NSN   1ADQ        0        42  0.146161   
15          15       1v1   1NSN   1FBI        0        42  0.148872   
16          16       1v1   1NSN   2YPV        0        42  0.158803   
17          17       1v1   1NSN   1OB1        0        42  0.238344   
18          18       1v1   3RAJ   3VRL        0        42  0.191761   
19          19       1v1   3RAJ   1NSN        0        42 -0.024960   

                p        r2     r_pos  ...  logits_pos_std  Energy_pos_mean  \
0    0.000000e+00  0.342285 -0.585052  ...        6.624078       -98.309468   
1   2.828910e-131  0.112130 -0.334859  ...        4.636723       -98.309468   
2    6.265870e-27  0.022837 -0.151120  ...        6.124475       -98.309468   
3    0.000000e+00  0.272969 -0.522465  ...        7.849567       -98.309468   
4    0.000000e+00  0.288529 -0.537149  ...        6.376433       -98.309468   
5   9.707416e-288  0.231222 -0.480855  ...        5.924564       -98.309468   
6   1.143578e-157  0.133432 -0.365283  ...        8.455745       -98.309468   
7    0.000000e+00  0.338358 -0.581685  ...        7.275000       -98.309468   
8    0.000000e+00  0.376208 -0.613358  ...        6.252044       -98.309468   
9   5.443265e-114  0.097902  0.312892  ...       12.074571       -91.759442   
10   6.331222e-78  0.067489  0.259787  ...       14.322002       -91.759442   
11   2.070429e-43  0.037470  0.193571  ...       10.214824       -91.759442   
12   6.875031e-01  0.000032  0.005690  ...       10.128808       -91.759442   
13   1.361613e-87  0.075738  0.275205  ...       11.727607       -91.759442   
14   2.799786e-25  0.021363  0.146161  ...        9.478396       -91.759442   
15   3.563805e-26  0.022163  0.148872  ...       11.101193       -91.759442   
16   1.341736e-29  0.025218  0.158803  ...       10.065671       -91.759442   
17   1.583956e-65  0.056808  0.238344  ...        6.843073       -91.759442   
18   1.276598e-42  0.036772  0.191761  ...        5.804461      -101.782686   
19   7.760639e-02  0.000623 -0.024960  ...        4.284580      -101.782686   

    Energy_pos_std  logits_neg_mean  logits_neg_std  Energy_neg_mean  \
0         1.678374              NaN             NaN              NaN   
1         1.678374              NaN             NaN              NaN   
2         1.678374              NaN             NaN              NaN   
3         1.678374              NaN             NaN              NaN   
4         1.678374              NaN             NaN              NaN   
5         1.678374              NaN             NaN              NaN   
6         1.678374              NaN             NaN              NaN   
7         1.678374              NaN             NaN              NaN   
8         1.678374              NaN             NaN              NaN   
9         1.691842              NaN             NaN              NaN   
10        1.691842              NaN             NaN         

In [6]:
df_rd_attr = pd.read_csv(
    "../data/Frozen_MiniAbsolut_ML/07e_EnergyContributions.tsv",
    sep='\t',
)
df_rd_attr["rd_type"] = "attributions"
df_rd_attr["rd_metric"] = df_rd_attr["mean_pos_total"]
df_rd_attr.head()

task_type ag_pos ag_neg  seed_id  split_id      mean       std  mean_pos  \
0       1v1   3VRL   1NSN        0        42 -0.625605  0.157186 -0.625605   
1       1v1   3VRL   3RAJ        0        42 -0.415575  0.209052 -0.415575   
2       1v1   3VRL   5E94        0        42  0.002736  0.239668  0.002736   
3       1v1   3VRL   1H0D        0        42 -0.615945  0.121352 -0.615945   
4       1v1   3VRL   1WEJ        0        42 -0.547776  0.151417 -0.547776   

    std_pos  mean_neg  ...  mean_neg_fold  std_neg_fold  mean_total  \
0  0.157186       NaN  ...            NaN           NaN   -0.597005   
1  0.209052       NaN  ...            NaN           NaN   -0.404372   
2  0.239668       NaN  ...            NaN           NaN    0.091077   
3  0.121352       NaN  ...            NaN           NaN   -0.548198   
4  0.151417       NaN  ...            NaN           NaN   -0.532763   

   std_total  mean_pos_total  std_pos_total  mean_neg_total  std_neg_total  \
0   0.129539       -0.597005       0.129539             NaN            NaN   
1   0.219243       -0.404372       0.219243             NaN            NaN   
2   0.239068        0.091077       0.239068             NaN            NaN   
3   0.115280       -0.548198       0.115280             NaN            NaN   
4   0.169650       -0.532763       0.169650             NaN            NaN   

        rd_type  rd_metric  
0  attributions  -0.597005  
1  attributions  -0.404372  
2  attributions   0.091077  
3  attributions  -0.548198  
4  attributions  -0.532763  

[5 rows x 25 columns]

ID ~ RD

In [7]:
df_rd_attr_m = pd.merge(
    df_rd_attr,
    df_id,
    on=["task_type", "ag_pos", "ag_neg"],
    how="inner",
)
# df_rd_attr_m.head()

df_rd_logits_m = pd.merge(
    df_rd_logits,
    df_id,
    on=["task_type", "ag_pos", "ag_neg"],
    how="inner",
)
# df_rd_attr_m.head()

df_rd = pd.concat([df_rd_attr_m, df_rd_logits_m], axis=0)

In [8]:
# Group by task_type, ag_pos, ag_neg and average by acc and rd_metric, keep
# all these columns preserved
df_rd_id_agg = df_rd.groupby(["task_type", "ag_pos", "ag_neg", "rd_type"])[["acc", "rd_metric"]].median().reset_index()
df_rd_id_agg.head()

task_type ag_pos ag_neg       rd_type     acc  rd_metric
0       1v1   1ADQ   1FBI  attributions  0.9810   0.376355
1       1v1   1ADQ   1FBI        logits  0.9810   0.000551
2       1v1   1ADQ   1H0D  attributions  0.9760  -0.423528
3       1v1   1ADQ   1H0D        logits  0.9760  -0.097075
4       1v1   1ADQ   1NSN  attributions  0.9759   0.010832

In [9]:
df_rd_id_agg.groupby(["rd_type", "task_type"])[["acc", "rd_metric"]].median().sort_values("acc").sort_values("rd_type")

acc  rd_metric
rd_type      task_type                          
attributions high_vs_looser  0.914500  -0.695615
             1v9             0.943472  -0.348821
             1v1             0.980900  -0.006491
             high_vs_95low   0.987900  -0.708280
logits       high_vs_looser  0.914500  -0.615692
             1v9             0.943472  -0.199509
             1v1             0.980900  -0.047297
             high_vs_95low   0.987900  -0.517552

RD ~ OOD

In [10]:
df_ood.head()

task_1                             task_2  \
0  HIGH_VS_95LOW__3VRL__auto__0__42   HIGH_VS_95LOW__3VRL__auto__0__42   
1  HIGH_VS_95LOW__3VRL__auto__0__42  HIGH_VS_LOOSER__3VRL__auto__0__42   
2  HIGH_VS_95LOW__3VRL__auto__0__42     ONE_VS_NINE__3VRL__auto__0__42   
3  HIGH_VS_95LOW__3VRL__auto__0__42   HIGH_VS_95LOW__3VRL__auto__1__42   
4  HIGH_VS_95LOW__3VRL__auto__0__42  HIGH_VS_LOOSER__3VRL__auto__1__42   

        acc  recall  precision        f1 ag_1_pos ag_2_pos ag_1_neg ag_2_neg  \
0  0.996600   0.998   0.995213  0.996605     3VRL     3VRL     auto     auto   
1  0.758500   0.998   0.674780  0.805163     3VRL     3VRL     auto     auto   
2  0.912356   0.998   0.852117  0.919307     3VRL     3VRL     auto     auto   
3  0.996600   0.998   0.995213  0.996605     3VRL     3VRL     auto     auto   
4  0.758500   0.998   0.674780  0.805163     3VRL     3VRL     auto     auto   

   seed_1  seed_2  split_1  split_2    ag    task_1_type     task_2_type  
0       0       0       42       42  3VRL  high_vs_95low   high_vs_95low  
1       0       0       42       42  3VRL  high_vs_95low  high_vs_looser  
2       0       0       42       42  3VRL  high_vs_95low             1v9  
3       0       1       42       42  3VRL  high_vs_95low   high_vs_95low  
4       0       1       42       42  3VRL  high_vs_95low  high_vs_looser

In [11]:
df_rd_logits = pd.read_csv(
    "../data/Frozen_MiniAbsolut_ML/07e_LogitEnergyCorrelations_final.tsv",
)
df_rd_logits["rd_type"] = "logits"
df_rd_logits["rd_metric"] = df_rd_logits["r_pos"]


df_rd_attr = pd.read_csv(
    "../data/Frozen_MiniAbsolut_ML/07e_EnergyContributions.tsv",
    sep='\t',
)
df_rd_attr["rd_type"] = "attributions"
df_rd_attr["rd_metric"] = df_rd_attr["mean_pos_total"]


df_rd_attr_m = pd.merge(
    df_rd_attr,
    df_ood,
    left_on=["task_type", "ag_pos", "ag_neg"],
    right_on=["task_1_type", "ag_1_pos", "ag_1_neg"],
    how="inner",
)

df_rd_logits_m = pd.merge(
    df_rd_logits,
    df_ood,
    left_on=["task_type", "ag_pos", "ag_neg"],
    right_on=["task_1_type", "ag_1_pos", "ag_1_neg"],
    how="inner",
)
# df_rd_attr_m.head()

df_rd = pd.concat([df_rd_attr_m, df_rd_logits_m], axis=0)
df_rd.head()

task_type ag_pos ag_neg  seed_id  split_id      mean       std  mean_pos  \
0       1v1   3VRL   1NSN        0        42 -0.625605  0.157186 -0.625605   
1       1v1   3VRL   1NSN        0        42 -0.625605  0.157186 -0.625605   
2       1v1   3VRL   1NSN        0        42 -0.625605  0.157186 -0.625605   
3       1v1   3VRL   1NSN        0        42 -0.625605  0.157186 -0.625605   
4       1v1   3VRL   1NSN        0        42 -0.625605  0.157186 -0.625605   

    std_pos  mean_neg  ...  Energy_std  logits_pos_mean  logits_pos_std  \
0  0.157186       NaN  ...         NaN              NaN             NaN   
1  0.157186       NaN  ...         NaN              NaN             NaN   
2  0.157186       NaN  ...         NaN              NaN             NaN   
3  0.157186       NaN  ...         NaN              NaN             NaN   
4  0.157186       NaN  ...         NaN              NaN             NaN   

   Energy_pos_mean  Energy_pos_std  logits_neg_mean  logits_neg_std  \
0              NaN             NaN              NaN             NaN   
1              NaN             NaN              NaN             NaN   
2              NaN             NaN              NaN             NaN   
3              NaN             NaN              NaN             NaN   
4              NaN             NaN              NaN             NaN   

   Energy_neg_mean  Energy_neg_std  corr_type  
0              NaN             NaN        NaN  
1              NaN             NaN        NaN  
2              NaN             NaN        NaN  
3              NaN             NaN        NaN  
4              NaN             NaN        NaN  

[5 rows x 66 columns]

In [12]:
assert all(df_rd["ag_1_pos"] == df_rd["ag_2_pos"])

# Remove "OOD" with task_1 type == task_2 type
df_rd = df_rd.loc[(df_rd["task_1_type"] != df_rd["task_2_type"])].copy()


col_sel = [
    "task_1_type",
    "ag_1_pos",
    "ag_1_neg",
    "seed_1",
    "split_1",
    "task_2_type",
    "ag_2_pos",
    "ag_2_neg",
    "seed_2",
    "split_2",
    "acc",
    "rd_metric",
    "rd_type",
]
df_rd[col_sel]

task_1_type ag_1_pos ag_1_neg  seed_1  split_1     task_2_type  \
0                  1v1     3VRL     1NSN       0       42   high_vs_95low   
1                  1v1     3VRL     1NSN       0       42  high_vs_looser   
2                  1v1     3VRL     1NSN       0       42             1v9   
3                  1v1     3VRL     1NSN       0       42   high_vs_95low   
4                  1v1     3VRL     1NSN       0       42  high_vs_looser   
...                ...      ...      ...     ...      ...             ...   
349913  high_vs_looser     1OB1     auto       0        4             1v9   
349914  high_vs_looser     1OB1     auto       0        4   high_vs_95low   
349916  high_vs_looser     1OB1     auto       0        4             1v9   
349917  high_vs_looser     1OB1     auto       0        4   high_vs_95low   
349919  high_vs_looser     1OB1     auto       0        4             1v9   

       ag_2_pos ag_2_neg  seed_2  split_2       acc  rd_metric       rd_type  
0          3VRL     auto       0       42  0.979800  -0.597005  attributions  
1          3VRL     auto       0       42  0.677100  -0.597005  attributions  
2          3VRL     auto       0       42  0.879140  -0.597005  attributions  
3          3VRL     auto       1       42  0.979800  -0.597005  attributions  
4          3VRL     auto       1       42  0.677100  -0.597005  attributions  
...         ...      ...     ...      ...       ...        ...           ...  
349913     1OB1     auto       0        2  0.920160  -0.651385        logits  
349914     1OB1     auto       0        3  0.962200  -0.651385        logits  
349916     1OB1     auto       0        3  0.919860  -0.651385        logits  
349917     1OB1     auto       0        4  0.959200  -0.651385        logits  
349919     1OB1     auto       0        4  0.916558  -0.651385        logits  

[524880 rows x 13 columns]

In [13]:
# Aggregate ood
df_rd_ood_agg = df_rd.groupby(["task_1_type", "ag_1_pos", "ag_1_neg", "task_2_type", "ag_2_pos", "ag_2_neg", "rd_type"])[["acc", "rd_metric"]].median().reset_index()
print(df_rd_ood_agg.shape)
df_rd_ood_agg.head()

(1200, 9)


task_1_type ag_1_pos ag_1_neg     task_2_type ag_2_pos ag_2_neg  \
0         1v1     1ADQ     1FBI             1v9     1ADQ     auto   
1         1v1     1ADQ     1FBI             1v9     1ADQ     auto   
2         1v1     1ADQ     1FBI   high_vs_95low     1ADQ     auto   
3         1v1     1ADQ     1FBI   high_vs_95low     1ADQ     auto   
4         1v1     1ADQ     1FBI  high_vs_looser     1ADQ     auto   

        rd_type       acc  rd_metric  
0  attributions  0.590495   0.376355  
1        logits  0.590495   0.000551  
2  attributions  0.512800   0.376355  
3        logits  0.512800   0.000551  
4  attributions  0.545300   0.376355

In [15]:
from itertools import permutations
from scipy.stats import pearsonr

task_types = df_rd_ood_agg["task_1_type"].unique()
cmap = visualisations.PlotParams.cmap_tasks

fig, axs = plt.subplots(ncols=4, nrows=4, figsize=(8*3.14, 8*3.14), dpi=600)

for i in range(0, len(task_types)):
    for j in range(0, len(task_types)):
        
        if i == j:
            # Parameters for id, based on the plots from above.
            task = task_types[i]
            df_rd_i = df_rd_id_agg.query("task_type == @task") # .loc[~df_rd["is_indistribution"]]
            plot_title = f"{task}"
            xlabel = "ID accuracy"
        else:
            # Parameteres for ood
            task_1 = task_types[i]
            task_2 = task_types[j]
            df_rd_i = df_rd_ood_agg.query("task_1_type == @task_1 and task_2_type == @task_2")
            plot_title = f"{task_1} -> {task_2}"
            xlabel = "OOD accuracy"

        ax = axs[i, j]
        for k, (rd_type, df_g) in enumerate(df_rd_i.groupby("rd_type")):
            color = cmap[k] # type: ignore
            sns.regplot(
                x="acc",
                y="rd_metric",
                data=df_g,
                scatter=True,
                color=color,
                ax=ax,
                label=rd_type,
            )

            # Compute Pearson correlation
            r, pval = pearsonr(df_g["acc"], df_g["rd_metric"])
            slope, intercept = np.polyfit(df_g["acc"], df_g["rd_metric"], 1)
            
            # Add text with r, R2 and pval
            # Centroid
            x_c = df_g["acc"].mean()
            y_c = df_g["rd_metric"].mean()
            x_range = df_g["acc"].max() - df_g["acc"].min()

            # Separate text reliably
            if k == 0:
                # Move to left along regression line
                x = x_c - 0.3 * x_range
                y = slope * x + intercept
            else:
                # Move to right along regression line
                x = x_c + 0.1 * x_range
                y = slope * x + intercept

            ax.text(x, y, f"r={r:.2f}, $R^2$={r**2:.2f}\np={pval**2:.2f}", fontsize=12, fontweight="bold", color="black");


        ax.set_title(plot_title, fontsize=12)
        ax.set_xlabel(xlabel, fontsize=10)
        if j == 0:
            ax.set_ylabel("RD $r_{Energy, {Logits || Attributions}}$", fontsize=12)
        else:
            ax.set_ylabel(None)
        ax.set_ylim(-1.0, 1.0)

        # Legend location under the plot
        if i == j == 3:
            ax.legend(
                bbox_to_anchor=(0.5, -0.3),
                loc="center",
                borderaxespad=0.0,
                fontsize=7,
                title="RD Type",
                title_fontsize=8,
                ncol=10,
                frameon=False,
            )

In [16]:
records = []
for i in range(0, len(task_types)):
    for j in range(0, len(task_types)):
        
        if i == j:
            # Parameters for id, based on the plots from above.
            task = task_types[i]
            task_1 = task
            task_2 = task
            df_rd_i = df_rd_id_agg.query("task_type == @task") # .loc[~df_rd["is_indistribution"]]
        else:
            # Parameteres for ood
            task_1 = task_types[i]
            task_2 = task_types[j]
            df_rd_i = df_rd_ood_agg.query("task_1_type == @task_1 and task_2_type == @task_2")

        # Compute per RD type
        for k, (rd_type, df_g) in enumerate(df_rd_i.groupby("rd_type")):
            # Compute Pearson correlation
            r, pval = pearsonr(df_g["acc"], df_g["rd_metric"])
            records.append({
                "task_1": task_1,
                "task_2": task_2,
                "is_id": task_1 == task_2,
                "is_ood": task_1 != task_2,
                "rd_type": rd_type,
                "r": r,
                "r2": r ** 2,
                "pval": pval,
                "significant": pval < 0.05,
            })

df_rd_agg_corr = pd.DataFrame.from_records(records)
df_rd_agg_corr.sort_values(["rd_type", "is_ood"])

task_1          task_2  is_id  is_ood       rd_type         r  \
0              1v1             1v1   True   False  attributions  0.010980   
10             1v9             1v9   True   False  attributions -0.018999   
20   high_vs_95low   high_vs_95low   True   False  attributions -0.125285   
30  high_vs_looser  high_vs_looser   True   False  attributions -0.245400   
2              1v1             1v9  False    True  attributions -0.355915   
4              1v1   high_vs_95low  False    True  attributions -0.942645   
6              1v1  high_vs_looser  False    True  attributions -0.674573   
8              1v9             1v1  False    True  attributions -0.063959   
12             1v9   high_vs_95low  False    True  attributions -0.983291   
14             1v9  high_vs_looser  False    True  attributions -0.821049   
16   high_vs_95low             1v1  False    True  attributions  0.205415   
18   high_vs_95low             1v9  False    True  attributions  0.329103   
22   high_vs_95low  high_vs_looser  False    True  attributions  0.544661   
24  high_vs_looser             1v1  False    True  attributions -0.176405   
26  high_vs_looser             1v9  False    True  attributions -0.227879   
28  high_vs_looser   high_vs_95low  False    True  attributions -0.262089   
1              1v1             1v1   True   False        logits -0.080528   
11             1v9             1v9   True   False        logits -0.296256   
21   high_vs_95low   high_vs_95low   True   False        logits -0.825450   
31  high_vs_looser  high_vs_looser   True   False        logits -0.765335   
3              1v1             1v9  False    True        logits -0.451304   
5              1v1   high_vs_95low  False    True        logits -0.895370   
7              1v1  high_vs_looser  False    True        logits -0.741750   
9              1v9             1v1  False    True        logits -0.271144   
13             1v9   high_vs_95low  False    True        logits -0.894540   
15             1v9  high_vs_looser  False    True        logits -0.861013   
17   high_vs_95low             1v1  False    True        logits -0.478205   
19   high_vs_95low             1v9  False    True        logits -0.763929   
23   high_vs_95low  high_vs_looser  False    True        logits -0.441621   
25  high_vs_looser             1v1  False    True        logits -0.579776   
27  high_vs_looser             1v9  False    True        logits -0.750432   
29  high_vs_looser   high_vs_95low  False    True        logits -0.818327   

          r2          pval  significant  
0   0.000121  9.181896e-01        False  
10  0.000361  9.584557e-01        False  
20  0.015696  7.302001e-01        False  
30  0.060221  4.943631e-01        False  
2   0.126676  5.757872e-04         True  
4   0.888581  1.046652e-43         True  
6   0.455048  3.115898e-13         True  
8   0.004091  5.492399e-01        False  
12  0.966861  3.342564e-07         True  
14  0.674121  3.593129e-03         True  
16  0.042195  5.210557e-02        False  
18  0.108309  3.531237e-01        False  
22  0.296656  1.035351e-01        False  
24  0.031119  9.627242e-02        False  
26  0.051929  5.266031e-01        False  
28  0.068690  4.644661e-01        False  
1   0.006485  4.505454e-01        False  
11  0.087768  4.058852e-01        False  
21  0.681367  3.270919e-03         True  
31  0.585738  9.884003e-03         True  
3   0.203675  8.031160e-06         True  
5   0.801688  1.144563e-32         True  
7   0.550193  6.130533e-17         True  
9   0.073519  9.739197e-03         True  
13  0.800203  4.756361e-04         True  
15  0.741343  1.375752e-03         True  
17  0.228680  1.871438e-06         True  
19  0.583587  1.010447e-02         True  
23  0.195029  2.013386e-01        False  
25  0.336140  2.125659e-09         True  
27  0.563148  1.239891e-02         True  
29  0.669659  3.803481e-03         True

In [17]:
# Convert task names to clean
df_rd_agg_corr["task_1"] = df_rd_agg_corr["task_1"].apply(lambda x: visualisations.map_task_type_to_clean[x])
df_rd_agg_corr["task_2"] = df_rd_agg_corr["task_2"].apply(lambda x: visualisations.map_task_type_to_clean[x])
df_rd_agg_corr.sort_values(["rd_type", "is_ood"])

task_1         task_2  is_id  is_ood       rd_type         r  \
0            vs 1           vs 1   True   False  attributions  0.010980   
10           vs 9           vs 9   True   False  attributions -0.018999   
20  vs Non-binder  vs Non-binder   True   False  attributions -0.125285   
30        vs Weak        vs Weak   True   False  attributions -0.245400   
2            vs 1           vs 9  False    True  attributions -0.355915   
4            vs 1  vs Non-binder  False    True  attributions -0.942645   
6            vs 1        vs Weak  False    True  attributions -0.674573   
8            vs 9           vs 1  False    True  attributions -0.063959   
12           vs 9  vs Non-binder  False    True  attributions -0.983291   
14           vs 9        vs Weak  False    True  attributions -0.821049   
16  vs Non-binder           vs 1  False    True  attributions  0.205415   
18  vs Non-binder           vs 9  False    True  attributions  0.329103   
22  vs Non-binder        vs Weak  False    True  attributions  0.544661   
24        vs Weak           vs 1  False    True  attributions -0.176405   
26        vs Weak           vs 9  False    True  attributions -0.227879   
28        vs Weak  vs Non-binder  False    True  attributions -0.262089   
1            vs 1           vs 1   True   False        logits -0.080528   
11           vs 9           vs 9   True   False        logits -0.296256   
21  vs Non-binder  vs Non-binder   True   False        logits -0.825450   
31        vs Weak        vs Weak   True   False        logits -0.765335   
3            vs 1           vs 9  False    True        logits -0.451304   
5            vs 1  vs Non-binder  False    True        logits -0.895370   
7            vs 1        vs Weak  False    True        logits -0.741750   
9            vs 9           vs 1  False    True        logits -0.271144   
13           vs 9  vs Non-binder  False    True        logits -0.894540   
15           vs 9        vs Weak  False    True        logits -0.861013   
17  vs Non-binder           vs 1  False    True        logits -0.478205   
19  vs Non-binder           vs 9  False    True        logits -0.763929   
23  vs Non-binder        vs Weak  False    True        logits -0.441621   
25        vs Weak           vs 1  False    True        logits -0.579776   
27        vs Weak           vs 9  False    True        logits -0.750432   
29        vs Weak  vs Non-binder  False    True        logits -0.818327   

          r2          pval  significant  
0   0.000121  9.181896e-01        False  
10  0.000361  9.584557e-01        False  
20  0.015696  7.302001e-01        False  
30  0.060221  4.943631e-01        False  
2   0.126676  5.757872e-04         True  
4   0.888581  1.046652e-43         True  
6   0.455048  3.115898e-13         True  
8   0.004091  5.492399e-01        False  
12  0.966861  3.342564e-07         True  
14  0.674121  3.593129e-03         True  
16  0.042195  5.210557e-02        False  
18  0.108309  3.531237e-01        False  
22  0.296656  1.035351e-01        False  
24  0.031119  9.627242e-02        False  
26  0.051929  5.266031e-01        False  
28  0.068690  4.644661e-01        False  
1   0.006485  4.505454e-01        False  
11  0.087768  4.058852e-01        False  
21  0.681367  3.270919e-03         True  
31  0.585738  9.884003e-03         True  
3   0.203675  8.031160e-06         True  
5   0.801688  1.144563e-32         True  
7   0.550193  6.130533e-17         True  
9   0.073519  9.739197e-03         True  
13  0.800203  4.756361e-04         True  
15  0.741343  1.375752e-03         True  
17  0.228680  1.871438e-06         True  
19  0.583587  1.010447e-02         True  
23  0.195029  2.013386e-01        False  
25  0.336140  2.125659e-09         True  
27  0.563148  1.239891e-02         True  
29  0.669659  3.803481e-03         True